In [2]:
!git clone https://github.com/indobenchmark/indonlu.git
!pip install transformers
!pip install -U 'scikit-learn<0.24'
!pip install sklearn-crfsuite

Cloning into 'indonlu'...
remote: Enumerating objects: 427, done.
remote: Counting objects: 100% (33/33), done.
remote: Compressing objects: 100% (19/19), done.
remote: Total 427 (delta 14), reused 30 (delta 14), pack-reused 394
Receiving objects: 100% (427/427), 4.83 MiB | 7.35 MiB/s, done.
Resolving deltas: 100% (209/209), done.
     |████████████████████████████████| 3.8 MB 4.0 MB/s 
     |████████████████████████████████| 895 kB 33.1 MB/s 
     |████████████████████████████████| 596 kB 33.9 MB/s 
     |████████████████████████████████| 67 kB 2.8 MB/s 
     |████████████████████████████████| 6.5 MB 35.5 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
     |████████████████████████████████| 6.8 MB 4.3 MB/s 
  Attempting uninstall: scikit-learn
    Found existing installation: scikit-learn 1.0.2
    Uninstalling scikit-learn-1.0.2:
      Successfully uninstalled scikit-learn-1.0.

In [18]:
!git clone https://github.com/indobenchmark/indonlu.git


fatal: destination path 'indonlu' already exists and is not an empty directory.


# Import Library

In [3]:
import os, sys
sys.path.append('../')
os.chdir('../')

import random
import numpy as np
import pandas as pd
import torch
from torch import optim
from tqdm import tqdm

from transformers import BertConfig, BertTokenizer
from nltk.tokenize import word_tokenize

In [4]:
from torch import nn
from torch.nn import CrossEntropyLoss, MSELoss

from transformers import BertPreTrainedModel, BertModel, BertConfig
from torch.utils.data import Dataset, DataLoader

import re
from collections import defaultdict, namedtuple

from indonlu.utils.conlleval import conll_evaluation
from gensim.models import Word2Vec

from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

import tensorflow as tf
from tensorflow.keras import Model,Input
from tensorflow.keras.layers import LSTM,Embedding,Dense
from tensorflow.keras.layers import TimeDistributed, SpatialDropout1D, Bidirectional
from tensorflow.keras.utils import to_categorical

from itertools import chain

import nltk
import sklearn
import scipy.stats

import sklearn_crfsuite
from sklearn_crfsuite import scorers,CRF
from sklearn_crfsuite.metrics import flat_classification_report
from sklearn_crfsuite import metrics

In [5]:
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

In [6]:
downloaded = drive.CreateFile({'id':"12mW6Xh3Qc-5YrzGb-rEEGuiDbsAY57xN"})   # replace the id with id of file you want to access
downloaded.GetContentFile('glove_50dim_wiki.id.case.text.txt')          
downloaded = drive.CreateFile({'id':"1fzjyyn0-OvGcegrnmRW_Ab6vf62HP2HT"})   # replace the id with id of file you want to access
downloaded.GetContentFile('idwiki_word2vec_200_new.tar.gz')

In [7]:
!tar -xf "/idwiki_word2vec_200_new.tar.gz"

In [8]:
# Static constant variable
LABEL2INDEX = {'O':0, 'B':1, 'I':2}
INDEX2LABEL = {0:'O', 1:'B', 2:'I'}
NUM_LABELS = 3
MAX_LEN = 110

# Traditional ML (CRF)


# Load Data



In [ ]:
def load_dataset(path):
    # Read file
    data = open(path,'r').readlines()

    # Prepare buffer
    all_df = pd.DataFrame()
    dataset = []
    sentence = []
    seq_label = []
    cnt = 1
    for line in data:
        if len(line.strip()) > 0:
            token, label = line[:-1].split('\t')
            sentence.append(token)
            seq_label.append(label)
        else:
            df = pd.DataFrame({
                'no':cnt,
                'word': sentence,
                'label': seq_label,
            })
            all_df = pd.concat([all_df,df])
            cnt+=1
            sentence = []
            seq_label = []
    return all_df

In [ ]:
train_dataset_path = '/content/indonlu/dataset/keps_keyword-extraction-prosa/train_preprocess.txt'
valid_dataset_path = '/content/indonlu/dataset/keps_keyword-extraction-prosa/valid_preprocess.txt'
test_dataset_path = '/content/indonlu/dataset/keps_keyword-extraction-prosa/test_preprocess_masked_label.txt'

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
train_data = load_dataset(train_dataset_path)
valid_data = load_dataset(valid_dataset_path)
test_data = load_dataset(test_dataset_path)

In [ ]:
train_data.head()

no     word label
0   1  Setelah     O
1   1  melalui     B
2   1   proses     B
3   1  telepon     I
4   1     yang     O

# Preprocess


In [ ]:
# A class to retrieve the sentences from the dataset
class getsentence(object):
    
    def __init__(self, data):
        self.data = data
        agg_func = lambda s: [(w, p) for w, p in zip(s["word"].values.tolist(),s["label"].values.tolist())]
        self.grouped = self.data.groupby("no").apply(agg_func)
        self.sentences = [s for s in self.grouped]

In [ ]:
train_getter = getsentence(train_data)
valid_getter = getsentence(valid_data)
test_getter = getsentence(test_data)

In [ ]:
# Feature set
def word2features(sent, i):
    word = sent[i][0]

    features = {
        'bias': 1.0,
        'word.lower()': word.lower(),
        'word[-3:]': word[-3:],
        'word[-2:]': word[-2:],
        'word.isdigit()': word.isdigit(),
        'word.isalnum()':word.isalnum(),
    }
    if i > 0:
        word1 = sent[i-1][0]
        features.update({
            '-1:word.lower()': word1.lower(),
            '-1:word.isalnum()':word1.isalnum(),
        })
    else:
        features['BOS'] = True

    if i < len(sent)-1:
        word1 = sent[i+1][0]
        features.update({
            '+1:word.lower()': word1.lower(),
            '+1:word.isalnum()':word1.isalnum(),
        })
    else:
        features['EOS'] = True

    return features

In [ ]:
def sent2features(sent):
    return [word2features(sent, i) for i in range(len(sent))]

def sent2labels(sent):
    return [label for _, label in sent]

In [ ]:
x_train = [sent2features(s) for s in train_getter.sentences]
y_train = [sent2labels(s) for s in train_getter.sentences]

x_valid = [sent2features(s) for s in valid_getter.sentences]
y_valid = [sent2labels(s) for s in valid_getter.sentences]

x_test = [sent2features(s) for s in test_getter.sentences]
y_test = [sent2labels(s) for s in test_getter.sentences]

In [ ]:
x_train

[[{'+1:word.isalnum()': True,
   '+1:word.lower()': 'melalui',
   'BOS': True,
   'bias': 1.0,
   'word.isalnum()': True,
   'word.isdigit()': False,
   'word.lower()': 'setelah',
   'word[-2:]': 'ah',
   'word[-3:]': 'lah'},
  {'+1:word.isalnum()': True,
   '+1:word.lower()': 'proses',
   '-1:word.isalnum()': True,
   '-1:word.lower()': 'setelah',
   'bias': 1.0,
   'word.isalnum()': True,
   'word.isdigit()': False,
   'word.lower()': 'melalui',
   'word[-2:]': 'ui',
   'word[-3:]': 'lui'},
  {'+1:word.isalnum()': True,
   '+1:word.lower()': 'telepon',
   '-1:word.isalnum()': True,
   '-1:word.lower()': 'melalui',
   'bias': 1.0,
   'word.isalnum()': True,
   'word.isdigit()': False,
   'word.lower()': 'proses',
   'word[-2:]': 'es',
   'word[-3:]': 'ses'},
  {'+1:word.isalnum()': True,
   '+1:word.lower()': 'yang',
   '-1:word.isalnum()': True,
   '-1:word.lower()': 'proses',
   'bias': 1.0,
   'word.isalnum()': True,
   'word.isdigit()': False,
   'word.lower()': 'telepon',
   'wor

# Modeling

In [ ]:
#Creating the CRF model
crf = CRF(algorithm='lbfgs',
          c1=0.1,
          c2=0.1,
          max_iterations=100,
          all_possible_transitions=False)

In [ ]:
crf.fit(x_train, y_train)

/usr/local/lib/python3.7/dist-packages/sklearn/base.py:213: FutureWarning: From version 0.24, get_params will raise an AttributeError if a parameter cannot be retrieved as an instance attribute. Previously it would return None.
  FutureWarning)


CRF(algorithm='lbfgs', all_possible_transitions=False, c1=0.1, c2=0.1,
    keep_tempfiles=None, max_iterations=100)

In [ ]:
y_pred_valid = crf.predict(x_valid)

In [ ]:
print(flat_classification_report(
    y_valid, y_pred_valid, digits=3
))

              precision    recall  f1-score   support

           B      0.781     0.784     0.782       763
           I      0.753     0.708     0.730       349
           O      0.856     0.868     0.862      1250

    accuracy                          0.817      2362
   macro avg      0.796     0.786     0.791      2362
weighted avg      0.816     0.817     0.817      2362



/usr/local/lib/python3.7/dist-packages/sklearn/utils/validation.py:70: FutureWarning: Pass labels=None as keyword args. From version 0.25 passing these as positional arguments will result in an error
  FutureWarning)


# Test

In [ ]:
y_pred_test = crf.predict(x_test)

In [ ]:
# Save prediction
df = pd.DataFrame({'label':y_pred_test}).reset_index()
df.to_csv('pred.txt', index=False)

print(df)

     index                                              label
0        0   [O, B, I, B, O, B, I, I, O, O, O, O, O, B, I, O]
1        1  [O, O, O, O, O, O, O, O, B, B, B, I, O, O, O, ...
2        2         [O, B, B, I, B, O, O, O, B, B, O, O, O, O]
3        3  [O, B, O, O, O, B, I, O, O, O, O, O, O, B, I, ...
4        4  [O, O, B, B, B, O, B, I, B, B, B, I, I, O, O, ...
..     ...                                                ...
242    242  [B, I, B, O, B, I, O, B, O, O, O, O, B, B, O, ...
243    243                     [B, B, O, O, O, O, B, I, O, O]
244    244  [O, B, B, O, B, O, O, O, B, B, O, O, O, O, O, ...
245    245  [O, B, B, O, B, B, I, I, B, O, O, O, O, O, O, ...
246    246                                       [B, B, I, B]

[247 rows x 2 columns]


# Non Contextual Embeddings (GLOVE + Bi-LSTM)

# Load Data

In [ ]:
def load_dataset(path):
    # Read file
    data = open(path,'r').readlines()

    # Prepare buffer
    dataset = []
    sentence = []
    seq_label = []
    for line in data:
        if len(line.strip()) > 0:
            token, label = line[:-1].split('\t')
            sentence.append(token)
            seq_label.append(LABEL2INDEX[label])
        else:
            dataset.append({
                'sentence_list': sentence,
                'seq_label': seq_label,
                # tambahan
                'sentence': " ".join(sentence)
            })
            sentence = []
            seq_label = []
    return pd.DataFrame(dataset)

In [ ]:
train_dataset_path = '/content/indonlu/dataset/keps_keyword-extraction-prosa/train_preprocess.txt'
valid_dataset_path = '/content/indonlu/dataset/keps_keyword-extraction-prosa/valid_preprocess.txt'
test_dataset_path = '/content/indonlu/dataset/keps_keyword-extraction-prosa/test_preprocess_masked_label.txt'

In [ ]:
train_data = load_dataset(train_dataset_path)
valid_data = load_dataset(valid_dataset_path)
test_data = load_dataset(test_dataset_path)

# Preprocess

In [ ]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(np.concatenate([train_data['sentence'],valid_data['sentence'],test_data['sentence']]))

In [ ]:
seq_train_data = tokenizer.texts_to_sequences(train_data['sentence'])
seq_val_data = tokenizer.texts_to_sequences(valid_data['sentence'])
seq_test_data = tokenizer.texts_to_sequences(test_data['sentence'])

In [ ]:
seq_train_label = pad_sequences(maxlen=MAX_LEN,sequences=train_data['seq_label'],padding="post",value=NUM_LABELS)
seq_val_label = pad_sequences(maxlen=MAX_LEN,sequences=valid_data['seq_label'],padding="post",value=NUM_LABELS)
seq_test_label = pad_sequences(maxlen=MAX_LEN,sequences=test_data['seq_label'],padding="post",value=NUM_LABELS)

In [ ]:
X_train = pad_sequences(seq_train_data,maxlen=MAX_LEN, padding='post')
y_train = np.array([to_categorical(i,num_classes = NUM_LABELS+1) for i in  seq_train_label])

In [ ]:
X_val = pad_sequences(seq_val_data,maxlen=MAX_LEN, padding='post')
y_val = np.array([to_categorical(i,num_classes = NUM_LABELS+1) for i in  seq_val_label])

In [ ]:
X_test = pad_sequences(seq_test_data,maxlen=MAX_LEN, padding='post')
y_test = np.array([to_categorical(i,num_classes = NUM_LABELS+1) for i in  seq_test_label])

In [ ]:
EMBEDDING_DIM=200
vocabulary_size=len(tokenizer.word_index)+1
embedding_matrix = np.zeros((vocabulary_size, EMBEDDING_DIM+2))

In [ ]:
#load vocabulary word2vec
word2vec = Word2Vec.load("/idwiki_word2vec_200_new_lower.model")
all_vocab = word2vec.wv.vocab.keys()

In [ ]:
for word, i in tokenizer.word_index.items():
  # embedding_vector = glove.get(word,np.random.uniform(low=-1, high=1, size=(EMBEDDING_DIM,)))
  if word in all_vocab:
    embedding_vector = word2vec.wv[word]
  else:
    embedding_vector = np.random.uniform(low=-1, high=1, size=(EMBEDDING_DIM,))
  embedding_matrix[i] = np.array(list(embedding_vector) + [word.isalnum(), word.isdigit()])
embedding_vector = np.random.uniform(low=-1, high=1, size=(EMBEDDING_DIM,))
embedding_matrix[0] = np.array(list(embedding_vector) + [0, 0])

# Modeling

In [ ]:
LSTM_UNITS=128

input = Input(shape = (MAX_LEN,))
model = Embedding(input_dim = vocabulary_size ,output_dim = EMBEDDING_DIM+2,input_length = MAX_LEN,weights=[embedding_matrix])(input)

model = Bidirectional(LSTM(units=LSTM_UNITS,return_sequences=True))(model)
out = TimeDistributed(Dense(NUM_LABELS+1,activation = 'softmax'))(model)
model = Model(input,out)
model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 110)]             0         
                                                                 
 embedding (Embedding)       (None, 110, 202)          457126    
                                                                 
 bidirectional (Bidirectiona  (None, 110, 256)         338944    
 l)                                                              
                                                                 
 time_distributed (TimeDistr  (None, 110, 4)           1028      
 ibuted)                                                         
                                                                 
Total params: 797,098
Trainable params: 797,098
Non-trainable params: 0
_________________________________________________________________


In [ ]:
model.compile(optimizer = 'adam',loss = 'categorical_crossentropy',metrics = ['accuracy'])

In [ ]:
history = model.fit(X_train,y_train,validation_data=(X_val,y_val),batch_size = 32,epochs = 7)

Epoch 1/7
25/25 [==============================] - 11s 122ms/step - loss: 0.1648 - accuracy: 0.9401 - val_loss: 0.0979 - val_accuracy: 0.9586
Epoch 2/7
25/25 [==============================] - 2s 78ms/step - loss: 0.0963 - accuracy: 0.9605 - val_loss: 0.0879 - val_accuracy: 0.9635
Epoch 3/7
25/25 [==============================] - 2s 79ms/step - loss: 0.0871 - accuracy: 0.9650 - val_loss: 0.0827 - val_accuracy: 0.9666
Epoch 4/7
25/25 [==============================] - 2s 79ms/step - loss: 0.0810 - accuracy: 0.9679 - val_loss: 0.0789 - val_accuracy: 0.9682
Epoch 5/7
25/25 [==============================] - 2s 79ms/step - loss: 0.0762 - accuracy: 0.9703 - val_loss: 0.0761 - val_accuracy: 0.9697
Epoch 6/7
25/25 [==============================] - 2s 79ms/step - loss: 0.0715 - accuracy: 0.9725 - val_loss: 0.0744 - val_accuracy: 0.9704
Epoch 7/7
25/25 [==============================] - 2s 78ms/step - loss: 0.0671 - accuracy: 0.9747 - val_loss: 0.0728 - val_accuracy: 0.9711


# Test

In [ ]:
y_pred = model.predict(X_val)

In [ ]:
y_pred = np.argmax(y_pred,axis=2)

In [ ]:
y_pred.shape

(200, 110)

In [ ]:
pred_label = []
for label in y_pred:
  pred = [i for i in label if i != 3]
  pred_label.append([INDEX2LABEL[i] for i in pred])

In [ ]:
actual_label = []
for label in seq_val_label:
  actual = [i for i in label if i != 3]
  actual_label.append([INDEX2LABEL[i] for i in actual])

In [ ]:
def keyword_extraction_metrics_fn(actual_label, pred_label):
    metrics = {}
    acc, pre, rec, f1, tm_pre, tm_rec, tm_f1 = conll_evaluation(actual_label, pred_label)
    metrics["ACC"] = acc
    metrics["F1"] = tm_f1
    metrics["REC"] = tm_rec
    metrics["PRE"] = tm_pre
    return metrics

In [ ]:
keyword_extraction_metrics_fn(actual_label, pred_label)

{'ACC': 0.7838375796178344,
 'F1': 0.5801033591731267,
 'PRE': 0.6026845637583893,
 'REC': 0.5591531755915318}

In [ ]:
# Save prediction
df = pd.DataFrame({'label':pred_label}).reset_index()
df.to_csv('pred.txt', index=False)

print(df)

     index                                              label
0        0                                             [B, I]
1        1                        [B, B, O, B, B, O, O, O, B]
2        2                                 [B, O, B, B, B, O]
3        3                           [B, I, I, O, O, B, B, B]
4        4  [B, O, B, B, I, O, B, O, O, O, B, B, O, O, B, ...
..     ...                                                ...
195    195  [B, O, B, I, O, O, B, O, O, B, O, O, O, B, O, ...
196    196                        [B, O, O, B, I, O, B, I, I]
197    197  [I, O, B, O, O, B, O, B, O, O, B, O, B, O, O, ...
198    198  [B, O, O, B, O, O, B, I, B, B, O, O, O, O, O, ...
199    199  [O, O, O, O, O, O, B, I, O, O, O, I, O, O, O, ...

[200 rows x 2 columns]


# Contextual Embeddings (BERT)

# Utils

In [9]:
class BertForWordClassification(BertPreTrainedModel):
    def __init__(self, config):
        super().__init__(config)
        self.num_labels = config.num_labels

        self.bert = BertModel(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)

        self.init_weights()

    def forward(
        self,
        input_ids=None,
        subword_to_word_ids=None,
        attention_mask=None,
        token_type_ids=None,
        position_ids=None,
        head_mask=None,
        inputs_embeds=None,
        labels=None,
    ):
        r"""
        labels (:obj:`torch.LongTensor` of shape :obj:`(batch_size, sequence_length)`, `optional`, defaults to :obj:`None`):
            Labels for computing the token classification loss.
            Indices should be in ``[0, ..., config.num_labels - 1]``.
    Returns:
        :obj:`tuple(torch.FloatTensor)` comprising various elements depending on the configuration (:class:`~transformers.BertConfig`) and inputs:
        loss (:obj:`torch.FloatTensor` of shape :obj:`(1,)`, `optional`, returned when ``labels`` is provided) :
            Classification loss.
        scores (:obj:`torch.FloatTensor` of shape :obj:`(batch_size, sequence_length, config.num_labels)`)
            Classification scores (before SoftMax).
        hidden_states (:obj:`tuple(torch.FloatTensor)`, `optional`, returned when ``config.output_hidden_states=True``):
            Tuple of :obj:`torch.FloatTensor` (one for the output of the embeddings + one for the output of each layer)
            of shape :obj:`(batch_size, sequence_length, hidden_size)`.
            Hidden-states of the model at the output of each layer plus the initial embedding outputs.
        attentions (:obj:`tuple(torch.FloatTensor)`, `optional`, returned when ``config.output_attentions=True``):
            Tuple of :obj:`torch.FloatTensor` (one for each layer) of shape
            :obj:`(batch_size, num_heads, sequence_length, sequence_length)`.
            Attentions weights after the attention softmax, used to compute the weighted average in the self-attention
            heads.
        """

        outputs = self.bert(
            input_ids,
            attention_mask=attention_mask,
            token_type_ids=token_type_ids,
            position_ids=position_ids,
            head_mask=head_mask,
            inputs_embeds=inputs_embeds,
        )

        sequence_output = outputs[0]

        # average the token-level outputs to compute word-level representations
        max_seq_len = subword_to_word_ids.max() + 1
        word_latents = []
        for i in range(max_seq_len):
            mask = (subword_to_word_ids == i).unsqueeze(dim=-1)
            word_latents.append((sequence_output * mask).sum(dim=1) / mask.sum())
        word_batch = torch.stack(word_latents, dim=1)

        sequence_output = self.dropout(word_batch)
        logits = self.classifier(sequence_output)

        outputs = (logits,) + outputs[2:]  # add hidden states and attention if they are here
        if labels is not None:
            loss_fct = CrossEntropyLoss()
            loss = loss_fct(logits.view(-1, self.num_labels), labels.view(-1))
            outputs = (loss,) + outputs

        return outputs  # (loss), scores, (hidden_states), (attentions)

In [10]:
# Forward function for word classification
def forward_word_classification(model, batch_data, i2w, is_test=False, device='cpu', **kwargs):
    # Unpack batch data
    if len(batch_data) == 4:
        (subword_batch, mask_batch, subword_to_word_indices_batch, label_batch) = batch_data
        token_type_batch = None
    elif len(batch_data) == 5:
        (subword_batch, mask_batch, token_type_batch, subword_to_word_indices_batch, label_batch) = batch_data
    
    # Prepare input & label
    subword_batch = torch.LongTensor(subword_batch)
    mask_batch = torch.FloatTensor(mask_batch)
    token_type_batch = torch.LongTensor(token_type_batch) if token_type_batch is not None else None
    subword_to_word_indices_batch = torch.LongTensor(subword_to_word_indices_batch)
    label_batch = torch.LongTensor(label_batch)

    if device == "cuda":
        subword_batch = subword_batch.cuda()
        mask_batch = mask_batch.cuda()
        token_type_batch = token_type_batch.cuda() if token_type_batch is not None else None
        subword_to_word_indices_batch = subword_to_word_indices_batch.cuda()
        label_batch = label_batch.cuda()

    # Forward model
    outputs = model(subword_batch, subword_to_word_indices_batch, attention_mask=mask_batch, token_type_ids=token_type_batch, labels=label_batch)
    loss, logits = outputs[:2]
    
    # generate prediction & label list
    list_hyps = []
    list_labels = []
    hyps_list = torch.topk(logits, k=1, dim=-1)[1].squeeze(dim=-1)
    for i in range(len(hyps_list)):
        hyps, labels = hyps_list[i].tolist(), label_batch[i].tolist()        
        list_hyp, list_label = [], []
        for j in range(len(hyps)):
            if labels[j] == -100:
                break
            else:
                list_hyp.append(i2w[hyps[j]])
                list_label.append(i2w[labels[j]])
        list_hyps.append(list_hyp)
        list_labels.append(list_label)
        
    return loss, list_hyps, list_labels

In [28]:
def keyword_extraction_metrics_fn(list_hyp, list_label):
    metrics = {}
    acc, pre, rec, f1, tm_pre, tm_rec, tm_f1 = conll_evaluation(list_hyp, list_label)
    metrics["ACC"] = acc
    metrics["F1"] = tm_f1
    metrics["REC"] = tm_rec
    metrics["PRE"] = tm_pre
    return metrics

In [12]:
#####
# Keyword Extraction Prosa
#####
class KeywordExtractionDataset(Dataset):
    # Static constant variable
    LABEL2INDEX = {'O':0, 'B':1, 'I':2}
    INDEX2LABEL = {0:'O', 1:'B', 2:'I'}
    NUM_LABELS = 3
    
    def load_dataset(self, path):
        # Read file
        data = open(path,'r').readlines()

        # Prepare buffer
        dataset = []
        sentence = []
        seq_label = []
        for line in data:
            if len(line.strip()) > 0:
                token, label = line[:-1].split('\t')
                sentence.append(token)
                seq_label.append(self.LABEL2INDEX[label])
            else:
                dataset.append({
                    'sentence': sentence,
                    'seq_label': seq_label
                })
                sentence = []
                seq_label = []
        return dataset
    
    def __init__(self, dataset_path, tokenizer, *args, **kwargs):
        self.data = self.load_dataset(dataset_path)
        self.tokenizer = tokenizer
        
    def __getitem__(self, index):
        data = self.data[index]
        sentence, seq_label = data['sentence'], data['seq_label']
        
        # Add CLS token
        subwords = [self.tokenizer.cls_token_id]
        subword_to_word_indices = [-1] # For CLS
        
        # Add subwords
        for word_idx, word in enumerate(sentence):
            subword_list = self.tokenizer.encode(word, add_special_tokens=False)
            subword_to_word_indices += [word_idx for i in range(len(subword_list))]
            subwords += subword_list
            
        # Add last SEP token
        subwords += [self.tokenizer.sep_token_id]
        subword_to_word_indices += [-1]
        
        return np.array(subwords), np.array(subword_to_word_indices), np.array(seq_label), data['sentence']
    
    def __len__(self):
        return len(self.data)
        
class KeywordExtractionDataLoader(DataLoader):
    def __init__(self, max_seq_len=512, *args, **kwargs):
        super(KeywordExtractionDataLoader, self).__init__(*args, **kwargs)
        self.collate_fn = self._collate_fn
        self.max_seq_len = max_seq_len
        
    def _collate_fn(self, batch):
        batch_size = len(batch)
        max_seq_len = max(map(lambda x: len(x[0]), batch))
        max_seq_len = min(self.max_seq_len, max_seq_len)
        max_tgt_len = max(map(lambda x: len(x[2]), batch))
        
        subword_batch = np.zeros((batch_size, max_seq_len), dtype=np.int64)
        mask_batch = np.zeros((batch_size, max_seq_len), dtype=np.float32)
        subword_to_word_indices_batch = np.full((batch_size, max_seq_len), -1, dtype=np.int64)
        seq_label_batch = np.full((batch_size, max_tgt_len), -100, dtype=np.int64)

        seq_list = []

        for i, (subwords, subword_to_word_indices, seq_label, raw_seq) in enumerate(batch):
            subwords = subwords[:max_seq_len]
            subword_to_word_indices = subword_to_word_indices[:max_seq_len]

            subword_batch[i,:len(subwords)] = subwords
            mask_batch[i,:len(subwords)] = 1
            subword_to_word_indices_batch[i,:len(subwords)] = subword_to_word_indices
            seq_label_batch[i,:len(seq_label)] = seq_label

            seq_list.append(raw_seq)
            
        return subword_batch, mask_batch, subword_to_word_indices_batch, seq_label_batch, seq_list

In [13]:
###
# common functions
###
def set_seed(seed):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    
def count_param(module, trainable=False):
    if trainable:
        return sum(p.numel() for p in module.parameters() if p.requires_grad)
    else:
        return sum(p.numel() for p in module.parameters())
    
def get_lr(optimizer):
    for param_group in optimizer.param_groups:
        return param_group['lr']

def metrics_to_string(metric_dict):
    string_list = []
    for key, value in metric_dict.items():
        string_list.append('{}:{:.2f}'.format(key, value))
    return ' '.join(string_list)

In [14]:
# Set random seed
set_seed(33221015)

# Load IndoBERT Model

In [15]:
# Load Tokenizer and Config
tokenizer = BertTokenizer.from_pretrained('indobenchmark/indobert-base-p1')
config = BertConfig.from_pretrained('indobenchmark/indobert-base-p1')
config.num_labels =  KeywordExtractionDataset.NUM_LABELS

# Instantiate model
model = BertForWordClassification.from_pretrained('indobenchmark/indobert-base-p1', config=config)

Downloading:   0%|          | 0.00/224k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/112 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.00 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.50k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/475M [00:00<?, ?B/s]

Some weights of BertForWordClassification were not initialized from the model checkpoint at indobenchmark/indobert-base-p1 and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


# Load Dataset

In [31]:
train_dataset_path = '/indonlu/dataset/keps_keyword-extraction-prosa/train_preprocess.txt'
valid_dataset_path = '/indonlu/dataset/keps_keyword-extraction-prosa/valid_preprocess.txt'
test_dataset_path = '/indonlu/dataset/keps_keyword-extraction-prosa/test_preprocess_masked_label.txt'

In [32]:
train_dataset = KeywordExtractionDataset(train_dataset_path, tokenizer, lowercase=True)
valid_dataset = KeywordExtractionDataset(valid_dataset_path, tokenizer, lowercase=True)
test_dataset = KeywordExtractionDataset(test_dataset_path, tokenizer, lowercase=True)

train_loader = KeywordExtractionDataLoader(dataset=train_dataset, max_seq_len=512, batch_size=16, num_workers=16, shuffle=True)  
valid_loader = KeywordExtractionDataLoader(dataset=valid_dataset, max_seq_len=512, batch_size=16, num_workers=16, shuffle=False)  
test_loader = KeywordExtractionDataLoader(dataset=test_dataset, max_seq_len=512, batch_size=16, num_workers=16, shuffle=False)

/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:481: UserWarning: This DataLoader will create 16 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))


In [33]:
w2i, i2w = KeywordExtractionDataset.LABEL2INDEX, KeywordExtractionDataset.INDEX2LABEL
print(w2i)
print(i2w)

{'O': 0, 'B': 1, 'I': 2}
{0: 'O', 1: 'B', 2: 'I'}


# Fine Tuning

In [34]:
optimizer = optim.Adam(model.parameters(), lr=2e-5)
model = model.cuda()

In [35]:
# Train
n_epochs = 5
for epoch in range(n_epochs):
    model.train()
    torch.set_grad_enabled(True)
 
    total_train_loss = 0
    list_hyp, list_label = [], []

    train_pbar = tqdm(train_loader, leave=True, total=len(train_loader))
    for i, batch_data in enumerate(train_pbar):
        # Forward model
        loss, batch_hyp, batch_label = forward_word_classification(model, batch_data[:-1], i2w=i2w, device='cuda')

        # Update model
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        tr_loss = loss.item()
        total_train_loss = total_train_loss + tr_loss

        # Calculate metrics
        list_hyp += batch_hyp
        list_label += batch_label

        train_pbar.set_description("(Epoch {}) TRAIN LOSS:{:.4f} LR:{:.8f}".format((epoch+1),
            total_train_loss/(i+1), get_lr(optimizer)))

    # Calculate train metric
    ukur = keyword_extraction_metrics_fn(list_hyp, list_label)
    print("(Epoch {}) TRAIN LOSS:{:.4f} {} LR:{:.8f}".format((epoch+1),
        total_train_loss/(i+1), metrics_to_string(ukur), get_lr(optimizer)))

    # Evaluate on validation
    model.eval()
    torch.set_grad_enabled(False)
    
    total_loss, total_correct, total_labels = 0, 0, 0
    list_hyp, list_label = [], []

    pbar = tqdm(valid_loader, leave=True, total=len(valid_loader))
    for i, batch_data in enumerate(pbar):
        batch_seq = batch_data[-1]        
        loss, batch_hyp, batch_label = forward_word_classification(model, batch_data[:-1], i2w=i2w, device='cuda')
        
        # Calculate total loss
        valid_loss = loss.item()
        total_loss = total_loss + valid_loss

        # Calculate evaluation metrics
        list_hyp += batch_hyp
        list_label += batch_label
        ukur = keyword_extraction_metrics_fn(list_hyp, list_label)

        pbar.set_description("VALID LOSS:{:.4f} {}".format(total_loss/(i+1), metrics_to_string(ukur)))
        
    ukur = keyword_extraction_metrics_fn(list_hyp, list_label)
    print("(Epoch {}) VALID LOSS:{:.4f} {}".format((epoch+1),
        total_loss/(i+1), metrics_to_string(ukur)))


  0%|          | 0/50 [00:00<?, ?it/s]/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:481: UserWarning: This DataLoader will create 16 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))
(Epoch 1) TRAIN LOSS:0.3620 LR:0.00002000: 100%|██████████| 50/50 [00:16<00:00,  3.12it/s]


(Epoch 1) TRAIN LOSS:0.3620 ACC:0.96 F1:0.91 REC:0.93 PRE:0.90 LR:0.00002000


VALID LOSS:0.6170 ACC:0.87 F1:0.75 REC:0.77 PRE:0.74: 100%|██████████| 13/13 [00:02<00:00,  4.84it/s]


(Epoch 1) VALID LOSS:0.6170 ACC:0.87 F1:0.75 REC:0.77 PRE:0.74


(Epoch 2) TRAIN LOSS:0.3402 LR:0.00002000: 100%|██████████| 50/50 [00:15<00:00,  3.15it/s]


...

(Epoch 4) VALID LOSS:0.6738 ACC:0.87 F1:0.75 REC:0.79 PRE:0.73


(Epoch 5) TRAIN LOSS:0.2980 LR:0.00002000: 100%|██████████| 50/50 [00:15<00:00,  3.15it/s]


(Epoch 5) TRAIN LOSS:0.2980 ACC:0.97 F1:0.93 REC:0.94 PRE:0.92 LR:0.00002000


VALID LOSS:0.7253 ACC:0.85 F1:0.71 REC:0.78 PRE:0.64: 100%|██████████| 13/13 [00:03<00:00,  4.12it/s]

(Epoch 5) VALID LOSS:0.7253 ACC:0.85 F1:0.71 REC:0.78 PRE:0.64


# Test

In [36]:
# Evaluate on test
model.eval()
torch.set_grad_enabled(False)

total_loss, total_correct, total_labels = 0, 0, 0
list_hyp, list_label = [], []

pbar = tqdm(test_loader, leave=True, total=len(test_loader))
for i, batch_data in enumerate(pbar):
    _, batch_hyp, _ = forward_word_classification(model, batch_data[:-1], i2w=i2w, device='cuda')
    list_hyp += batch_hyp

# Save prediction
df = pd.DataFrame({'label':list_hyp}).reset_index()
df.to_csv('pred.txt', index=False)

print(df)

  0%|          | 0/16 [00:00<?, ?it/s]/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:481: UserWarning: This DataLoader will create 16 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))
100%|██████████| 16/16 [00:03<00:00,  4.86it/s]

     index                                              label
0        0   [O, B, I, B, O, B, I, I, I, O, O, O, O, B, I, O]
1        1  [O, O, O, B, O, B, B, O, B, B, B, O, O, O, O, ...
2        2         [O, O, B, I, B, O, O, O, B, B, O, B, B, I]
3        3  [O, O, O, B, O, B, I, O, O, O, O, O, O, B, I, ...
4        4  [O, O, B, B, B, O, B, I, O, O, B, B, I, O, O, ...
..     ...                                                ...
242    242  [B, B, B, O, B, I, O, B, O, O, B, O, B, B, O, ...
243    243                     [B, B, O, B, I, O, B, I, I, I]
244    244  [O, B, B, O, B, I, I, I, B, B, O, O, O, O, O, ...
245    245  [O, B, B, O, B, B, I, I, I, I, O, O, O, O, O, ...
246    246                                       [B, B, I, B]

[247 rows x 2 columns]
